In [23]:
#import statements
import pandas as pd
import re
import ast
import mysql.connector
from mysql.connector import errorcode

In [39]:
# ---------- CONFIG SECTION ----------
DB_NAME = "videogames"
USER = "root"
PASSWORD = "Maha2301##"
HOST = "localhost"

In [25]:

# ---------- 1. LOAD DATA FROM EXCEL ----------

games_df = pd.read_csv("games.csv")
sales_df = pd.read_csv("vgsales.csv")


In [26]:
# ---------- 2. CLEANING AND NORMALIZATION ----------

# Remove unwanted index columns
games_df = games_df.loc[:, ~games_df.columns.str.contains('^Unnamed')]
sales_df = sales_df.loc[:, ~sales_df.columns.str.contains('^Unnamed')]

# Clean column names
games_df.columns = games_df.columns.str.strip().str.replace(" ", "_")
sales_df.columns = sales_df.columns.str.strip().str.replace(" ", "_")

# Drop duplicates
games_df.drop_duplicates(subset=["Title"], inplace=True)
sales_df.drop_duplicates(subset=["Name", "Platform", "Year"], inplace=True)


In [27]:
# Remove special characters like 'k', 'M', and commas
def clean_numeric(val):
    if pd.isnull(val):
        return 0
    if isinstance(val, str):
        val = val.replace(",", "").strip().lower()
        if val.endswith('k'):
            return int(float(val[:-1]) * 1000)
        elif val.endswith('m'):
            return int(float(val[:-1]) * 1_000_000)
        elif val.isdigit():
            return int(val)
        else:
            try:
                return int(float(val))
            except:
                return 0
    return int(val)



# Normalize genres and team (as comma-separated strings)
games_df['Genres'] = games_df['Genres'].astype(str).str.replace(r"[\[\]']", '', regex=True).str.lower().str.strip()
games_df['Team'] = games_df['Team'].astype(str).str.replace(r"[\[\]']", '', regex=True).str.lower().str.strip()
games_df['Rating'] = pd.to_numeric(games_df['Rating'], errors='coerce').fillna(0)

# Apply to numeric columns
for col in ["Plays", "Backlogs", "Wishlist","Playing"]:
    games_df[col] = games_df[col].apply(clean_numeric)

In [28]:
# # Fill nulls for numeric columns
# games_df['Rating'] = pd.to_numeric(games_df['Rating'], errors='coerce').fillna(0)
# games_df['Plays'] = pd.to_numeric(games_df['Plays'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)
# games_df['Wishlist'] = pd.to_numeric(games_df['Wishlist'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)
# games_df['Backlogs'] = pd.to_numeric(games_df['Backlogs'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)
# games_df['Playing'] = pd.to_numeric(games_df['Playing'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)
# games_df['Times Listed'] = pd.to_numeric(games_df['Times Listed'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)
# games_df['Number of Reviews'] = pd.to_numeric(games_df['Number of Reviews'].str.replace("K", "000", regex=False), errors='coerce').fillna(0)


In [29]:

# Handle missing values
games_df.fillna({
    "Rating": games_df["Rating"].mean(),
    "Plays": 0,
    "Backlogs": 0,
    "Wishlist": 0
}, inplace=True)
sales_df.fillna(0, inplace=True)

# Handle empty Ratings
games_df["Rating"] = pd.to_numeric(games_df["Rating"], errors="coerce").fillna(0)

# Clean special characters from text
def clean_text(text):
    if isinstance(text, str):
        return re.sub(r"[^\w\s\-&']", "", text)
    return text

for col in ["Title", "Summary"]:
    games_df[col] = games_df[col].apply(clean_text)
for col in ["Name", "Publisher"]:
    sales_df[col] = sales_df[col].apply(clean_text)

# Normalize date format
games_df["Release_Date"] = pd.to_datetime(games_df["Release_Date"], errors="coerce")

# Drop duplicates based only on 'Title'
games_df = games_df.drop_duplicates(subset=['Title'], keep='first').reset_index(drop=True)

# # Convert list strings to real lists
# games_df["Genres"] = games_df["Genres"].apply(lambda x: ast.literal_eval(x) if pd.notnull(x) else [])
# games_df["Team"] = games_df["Team"].apply(lambda x: ast.literal_eval(x) if pd.notnull(x) else [])

# Explode lists
genres_df = games_df[["Title", "Genres"]].explode("Genres").rename(columns={"Genres": "Genre"}).dropna()
devs_df = games_df[["Title", "Team"]].explode("Team").rename(columns={"Team": "Developer"}).dropna()


In [30]:

# Step 2: Remove duplicates based on normalized 'Title' (case-insensitive + trimmed)
games_df['Title'] = games_df['Title'].astype(str).str.strip()
games_df['Title_lower'] = games_df['Title'].str.lower()
games_df = games_df.drop_duplicates(subset='Title_lower', keep='first').drop(columns='Title_lower')

print(f"✅ Total rows after removing duplicates: {len(games_df)}")

✅ Total rows after removing duplicates: 1098


In [31]:
# ---------- 3. CONNECT TO MYSQL USING mysql.connector ----------

def create_connection():
    return mysql.connector.connect(
        host=HOST,
        user=USER,
        password=PASSWORD
    )

In [40]:
# Create DB
try:
    conn = create_connection()
    cursor = conn.cursor()
    cursor.execute(f"CREATE DATABASE IF NOT EXISTS {DB_NAME}")
    print(f"✅ Database '{DB_NAME}' is ready.")
    cursor.close()
    conn.close()
except mysql.connector.Error as err:
    print(f"❌ Error creating DB: {err}")


✅ Database 'videogames' is ready.


In [41]:
# Connect to new DB
conn = mysql.connector.connect(
    host=HOST,
    user=USER,
    password=PASSWORD,
    database=DB_NAME
)
cursor = conn.cursor()

In [42]:
# ---------- 4. CREATE TABLES ----------

TABLES = {}

TABLES['games'] = """
CREATE TABLE IF NOT EXISTS games (
    Title VARCHAR(255) PRIMARY KEY,
    Release_Date DATE,
    Rating FLOAT,
    Plays INT,
    Backlogs INT,
    Wishlist INT,
    Summary TEXT
)
"""

TABLES['sales'] = """
CREATE TABLE IF NOT EXISTS sales (
    Name VARCHAR(255),
    Platform VARCHAR(100),
    Year INT,
    Genre VARCHAR(100),
    Publisher VARCHAR(100),
    NA_Sales FLOAT,
    EU_Sales FLOAT,
    JP_Sales FLOAT,
    Other_Sales FLOAT,
    Global_Sales FLOAT
)
"""

TABLES['game_genres'] = """
CREATE TABLE IF NOT EXISTS game_genres (
    Title VARCHAR(255),
    Genre VARCHAR(100)
)
"""

TABLES['game_developers'] = """
CREATE TABLE IF NOT EXISTS game_developers (
    Title VARCHAR(255),
    Developer VARCHAR(100)
)
"""

In [43]:
# Execute table creation
for name, ddl in TABLES.items():
    try:
        cursor.execute(ddl)
        print(f"✅ Table '{name}' is ready.")
    except mysql.connector.Error as err:
        print(f"❌ Failed creating table {name}: {err}")

✅ Table 'games' is ready.
✅ Table 'sales' is ready.
✅ Table 'game_genres' is ready.
✅ Table 'game_developers' is ready.


In [45]:


# ---------- 5. INSERT CLEANED DATA ----------

def insert_dataframe(df, table):
    cols = ", ".join(df.columns)
    placeholders = ", ".join(["%s"] * len(df.columns))
    insert_query = f"INSERT INTO {table} ({cols}) VALUES ({placeholders})"

    for _, row in df.iterrows():
        try:
            cursor.execute(insert_query, tuple(row))
        except Exception as e:
            print(f"❌ Error inserting into {table}: {e}")

# Insert all
insert_dataframe(games_df[["Title", "Release_Date", "Rating", "Plays", "Backlogs", "Wishlist", "Summary"]], "games")
insert_dataframe(sales_df, "sales")
insert_dataframe(genres_df, "game_genres")
insert_dataframe(devs_df, "game_developers")



❌ Error inserting into games: 1062 (23000): Duplicate entry 'Elden Ring' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Hades' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'The Legend of Zelda Breath of the Wild' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Undertale' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Hollow Knight' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Minecraft' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Omori' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Metroid Dread' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'Among Us' for key 'games.PRIMARY'
❌ Error inserting into games: 1062 (23000): Duplicate entry 'NieR Automata' for key 'games.PRIMARY'
❌ Error

In [46]:
#Connection closure 
 
conn.commit()
cursor.close()
conn.close()

print("✅ All data inserted successfully.")

✅ All data inserted successfully.
